In [1]:
import torch
import pandas as pd
import numpy as np
import torch.nn as nn
import torchbnn as bnn
import torch.optim as optim
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
%matplotlib inline

In [2]:
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using {device} device")

Using cuda device


In [3]:
e_data = pd.read_csv("data.csv")
label = pd.read_csv("properity.csv")
conditions = ["materials", "color", "distance", "mode"]

In [4]:
e_data = e_data.drop(columns = conditions)
e_data = pd.concat([label, e_data], axis = 1)
e_data = e_data.drop(columns = ["Hardness", "Rigidity", "Strength"])
e_data

Density      names  spectrum_0  spectrum_1  spectrum_2  spectrum_3  \
0         0.7  Cardboard    0.526403    0.527891    0.529310    0.530688   
1         0.7  Cardboard    0.542235    0.543597    0.544961    0.546345   
2         0.7  Cardboard    0.536953    0.538290    0.539612    0.540949   
3         0.7  Cardboard    0.543379    0.544370    0.545400    0.546501   
4         0.7  Cardboard    0.523413    0.524326    0.525328    0.526431   
...       ...        ...         ...         ...         ...         ...   
1255      0.8       Wood    0.501132    0.501212    0.501278    0.501364   
1256      0.8       Wood    0.462299    0.462222    0.462148    0.462112   
1257      0.8       Wood    0.197083    0.197172    0.197252    0.197331   
1258      0.8       Wood    0.183714    0.183832    0.183919    0.183990   
1259      0.8       Wood    0.177628    0.177632    0.177647    0.177677   

      spectrum_4  spectrum_5  spectrum_6  spectrum_7  ...  spectrum_321  \
0       0.532068    0.533471    0.534901    0.536361  ...      0.670099   
1       0.547773    0.549250    0.550766    0.552315  ...      0.685934   
2       0.542335    0.543779    0.545277    0.546822  ...      0.679368   
3       0.547699    0.549000    0.550391    0.551859  ...      0.686358   
4       0.527640    0.528946    0.530326    0.531762  ...      0.661900   
...          ...         ...         ...         ...  ...           ...   
1255    0.501494    0.501661    0.501850    0.502045  ...      0.543924   
1256    0.462131    0.462201    0.462306    0.462434  ...      0.500846   
1257    0.197412    0.197492    0.197564    0.197624  ...      0.216179   
1258    0.184056    0.184118    0.184174    0.184224  ...      0.200452   
1259    0.177724    0.177783    0.177844    0.177903  ...      0.193133   

      spectrum_322  spectrum_323  spectrum_324  spectrum_325  spectrum_326  \
0         0.670870      0.671219      0.671284      0.671310      0.671274   
1         0.686723      0.687080      0.687148      0.687176      0.687140   
2         0.680120      0.680447      0.680490      0.680496      0.680442   
3         0.687150      0.687509      0.687577      0.687605      0.687568   
4         0.662690      0.663060      0.663147      0.663193      0.663175   
...            ...           ...           ...           ...           ...   
1255      0.544602      0.544929      0.545019      0.545072      0.545068   
1256      0.501468      0.501766      0.501847      0.501893      0.501888   
1257      0.216449      0.216579      0.216614      0.216634      0.216632   
1258      0.200693      0.200805      0.200831      0.200843      0.200835   
1259      0.193387      0.193515      0.193558      0.193585      0.193592   

      spectrum_327  spectrum_328  spectrum_329  spectrum_330  
0         0.671686      0.672272      0.672768      0.672819  
1         0.687564      0.688165      0.688675      0.688728  
2         0.680844      0.681425      0.681916      0.681958  
3         0.687990      0.688591      0.689099      0.689151  
4         0.663598      0.664191      0.664694      0.664755  
...            ...           ...           ...           ...  
1255      0.545425      0.545920      0.546338      0.546392  
1256      0.502214      0.502668      0.503051      0.503099  
1257      0.216773      0.216968      0.217133      0.217154  
1258      0.200960      0.201136      0.201285      0.201301  
1259      0.193726      0.193907      0.194060      0.194083  

[1260 rows x 333 columns]

In [5]:
# normalize data 
tep = e_data.loc[:, [ "names", "Density"]]
e_data_sp = e_data.copy().drop(columns = ['names', "Density"])
e_data_sp

spectrum_0  spectrum_1  spectrum_2  spectrum_3  spectrum_4  spectrum_5  \
0       0.526403    0.527891    0.529310    0.530688    0.532068    0.533471   
1       0.542235    0.543597    0.544961    0.546345    0.547773    0.549250   
2       0.536953    0.538290    0.539612    0.540949    0.542335    0.543779   
3       0.543379    0.544370    0.545400    0.546501    0.547699    0.549000   
4       0.523413    0.524326    0.525328    0.526431    0.527640    0.528946   
...          ...         ...         ...         ...         ...         ...   
1255    0.501132    0.501212    0.501278    0.501364    0.501494    0.501661   
1256    0.462299    0.462222    0.462148    0.462112    0.462131    0.462201   
1257    0.197083    0.197172    0.197252    0.197331    0.197412    0.197492   
1258    0.183714    0.183832    0.183919    0.183990    0.184056    0.184118   
1259    0.177628    0.177632    0.177647    0.177677    0.177724    0.177783   

      spectrum_6  spectrum_7  spectrum_8  spectrum_9  ...  spectrum_321  \
0       0.534901    0.536361    0.537855    0.539371  ...      0.670099   
1       0.550766    0.552315    0.553888    0.555468  ...      0.685934   
2       0.545277    0.546822    0.548405    0.550009  ...      0.679368   
3       0.550391    0.551859    0.553386    0.554947  ...      0.686358   
4       0.530326    0.531762    0.533235    0.534721  ...      0.661900   
...          ...         ...         ...         ...  ...           ...   
1255    0.501850    0.502045    0.502237    0.502413  ...      0.543924   
1256    0.462306    0.462434    0.462574    0.462712  ...      0.500846   
1257    0.197564    0.197624    0.197671    0.197703  ...      0.216179   
1258    0.184174    0.184224    0.184265    0.184299  ...      0.200452   
1259    0.177844    0.177903    0.177955    0.177997  ...      0.193133   

      spectrum_322  spectrum_323  spectrum_324  spectrum_325  spectrum_326  \
0         0.670870      0.671219      0.671284      0.671310      0.671274   
1         0.686723      0.687080      0.687148      0.687176      0.687140   
2         0.680120      0.680447      0.680490      0.680496      0.680442   
3         0.687150      0.687509      0.687577      0.687605      0.687568   
4         0.662690      0.663060      0.663147      0.663193      0.663175   
...            ...           ...           ...           ...           ...   
1255      0.544602      0.544929      0.545019      0.545072      0.545068   
1256      0.501468      0.501766      0.501847      0.501893      0.501888   
1257      0.216449      0.216579      0.216614      0.216634      0.216632   
1258      0.200693      0.200805      0.200831      0.200843      0.200835   
1259      0.193387      0.193515      0.193558      0.193585      0.193592   

      spectrum_327  spectrum_328  spectrum_329  spectrum_330  
0         0.671686      0.672272      0.672768      0.672819  
1         0.687564      0.688165      0.688675      0.688728  
2         0.680844      0.681425      0.681916      0.681958  
3         0.687990      0.688591      0.689099      0.689151  
4         0.663598      0.664191      0.664694      0.664755  
...            ...           ...           ...           ...  
1255      0.545425      0.545920      0.546338      0.546392  
1256      0.502214      0.502668      0.503051      0.503099  
1257      0.216773      0.216968      0.217133      0.217154  
1258      0.200960      0.201136      0.201285      0.201301  
1259      0.193726      0.193907      0.194060      0.194083  

[1260 rows x 331 columns]

In [6]:
e_data_sp = (e_data_sp - e_data_sp.mean(axis=0))/e_data_sp.std(axis=0)
e_data_sp

spectrum_0  spectrum_1  spectrum_2  spectrum_3  spectrum_4  spectrum_5  \
0       0.058279    0.063007    0.067694    0.072298    0.076858    0.081422   
1       0.107668    0.112021    0.116560    0.121207    0.125941    0.130761   
2       0.091189    0.095456    0.099860    0.104353    0.108945    0.113654   
3       0.111236    0.114431    0.117930    0.121694    0.125711    0.129980   
4       0.048949    0.051882    0.055263    0.058999    0.063017    0.067271   
...          ...         ...         ...         ...         ...         ...   
1255   -0.020559   -0.020252   -0.019827   -0.019304   -0.018699   -0.018044   
1256   -0.141702   -0.141929   -0.141998   -0.141924   -0.141726   -0.141434   
1257   -0.969075   -0.969072   -0.969058   -0.969057   -0.969083   -0.969153   
1258   -1.010783   -1.010703   -1.010686   -1.010730   -1.010826   -1.010971   
1259   -1.029769   -1.030050   -1.030271   -1.030452   -1.030616   -1.030782   

      spectrum_6  spectrum_7  spectrum_8  spectrum_9  ...  spectrum_321  \
0       0.086024    0.090695    0.095454    0.100302  ...      0.557489   
1       0.135658    0.140626    0.145654    0.150725  ...      0.610426   
2       0.118484    0.123433    0.128489    0.133625  ...      0.588477   
3       0.134483    0.139196    0.144083    0.149092  ...      0.611844   
4       0.071713    0.076300    0.080989    0.085738  ...      0.530075   
...          ...         ...         ...         ...  ...           ...   
1255   -0.017370   -0.016704   -0.016065   -0.015464  ...      0.135658   
1256   -0.141075   -0.140675   -0.140253   -0.139825  ...     -0.008360   
1257   -0.969274   -0.969449   -0.969673   -0.969936  ...     -0.960065   
1258   -1.011161   -1.011389   -1.011647   -1.011926  ...     -1.012643   
1259   -1.030964   -1.031170   -1.031404   -1.031664  ...     -1.037113   

      spectrum_322  spectrum_323  spectrum_324  spectrum_325  spectrum_326  \
0         0.557749      0.557980      0.558187      0.558372      0.558535   
1         0.610694      0.610936      0.611154      0.611349      0.611523   
2         0.588641      0.588790      0.588924      0.589045      0.589153   
3         0.612121      0.612367      0.612586      0.612779      0.612950   
4         0.530425      0.530738      0.531018      0.531267      0.531489   
...            ...           ...           ...           ...           ...   
1255      0.136021      0.136337      0.136612      0.136852      0.137061   
1256     -0.008045     -0.007770     -0.007532     -0.007325     -0.007146   
1257     -0.959989     -0.959924     -0.959869     -0.959823     -0.959784   
1258     -1.012611     -1.012586     -1.012566     -1.012551     -1.012540   
1259     -1.037013     -1.036925     -1.036849     -1.036784     -1.036727   

      spectrum_327  spectrum_328  spectrum_329  spectrum_330  
0         0.558680      0.558808      0.558920      0.559013  
1         0.611679      0.611817      0.611937      0.612038  
2         0.589249      0.589335      0.589409      0.589472  
3         0.613102      0.613235      0.613350      0.613446  
4         0.531685      0.531859      0.532009      0.532135  
...            ...           ...           ...           ...  
1255      0.137242      0.137398      0.137532      0.137642  
1256     -0.006990     -0.006856     -0.006743     -0.006649  
1257     -0.959750     -0.959722     -0.959699     -0.959680  
1258     -1.012531     -1.012525     -1.012520     -1.012517  
1259     -1.036678     -1.036636     -1.036601     -1.036572  

[1260 rows x 331 columns]

In [7]:
e_data = pd.concat([tep, e_data_sp], axis =1)
e_data

names  Density  spectrum_0  spectrum_1  spectrum_2  spectrum_3  \
0     Cardboard      0.7    0.058279    0.063007    0.067694    0.072298   
1     Cardboard      0.7    0.107668    0.112021    0.116560    0.121207   
2     Cardboard      0.7    0.091189    0.095456    0.099860    0.104353   
3     Cardboard      0.7    0.111236    0.114431    0.117930    0.121694   
4     Cardboard      0.7    0.048949    0.051882    0.055263    0.058999   
...         ...      ...         ...         ...         ...         ...   
1255       Wood      0.8   -0.020559   -0.020252   -0.019827   -0.019304   
1256       Wood      0.8   -0.141702   -0.141929   -0.141998   -0.141924   
1257       Wood      0.8   -0.969075   -0.969072   -0.969058   -0.969057   
1258       Wood      0.8   -1.010783   -1.010703   -1.010686   -1.010730   
1259       Wood      0.8   -1.029769   -1.030050   -1.030271   -1.030452   

      spectrum_4  spectrum_5  spectrum_6  spectrum_7  ...  spectrum_321  \
0       0.076858    0.081422    0.086024    0.090695  ...      0.557489   
1       0.125941    0.130761    0.135658    0.140626  ...      0.610426   
2       0.108945    0.113654    0.118484    0.123433  ...      0.588477   
3       0.125711    0.129980    0.134483    0.139196  ...      0.611844   
4       0.063017    0.067271    0.071713    0.076300  ...      0.530075   
...          ...         ...         ...         ...  ...           ...   
1255   -0.018699   -0.018044   -0.017370   -0.016704  ...      0.135658   
1256   -0.141726   -0.141434   -0.141075   -0.140675  ...     -0.008360   
1257   -0.969083   -0.969153   -0.969274   -0.969449  ...     -0.960065   
1258   -1.010826   -1.010971   -1.011161   -1.011389  ...     -1.012643   
1259   -1.030616   -1.030782   -1.030964   -1.031170  ...     -1.037113   

      spectrum_322  spectrum_323  spectrum_324  spectrum_325  spectrum_326  \
0         0.557749      0.557980      0.558187      0.558372      0.558535   
1         0.610694      0.610936      0.611154      0.611349      0.611523   
2         0.588641      0.588790      0.588924      0.589045      0.589153   
3         0.612121      0.612367      0.612586      0.612779      0.612950   
4         0.530425      0.530738      0.531018      0.531267      0.531489   
...            ...           ...           ...           ...           ...   
1255      0.136021      0.136337      0.136612      0.136852      0.137061   
1256     -0.008045     -0.007770     -0.007532     -0.007325     -0.007146   
1257     -0.959989     -0.959924     -0.959869     -0.959823     -0.959784   
1258     -1.012611     -1.012586     -1.012566     -1.012551     -1.012540   
1259     -1.037013     -1.036925     -1.036849     -1.036784     -1.036727   

      spectrum_327  spectrum_328  spectrum_329  spectrum_330  
0         0.558680      0.558808      0.558920      0.559013  
1         0.611679      0.611817      0.611937      0.612038  
2         0.589249      0.589335      0.589409      0.589472  
3         0.613102      0.613235      0.613350      0.613446  
4         0.531685      0.531859      0.532009      0.532135  
...            ...           ...           ...           ...  
1255      0.137242      0.137398      0.137532      0.137642  
1256     -0.006990     -0.006856     -0.006743     -0.006649  
1257     -0.959750     -0.959722     -0.959699     -0.959680  
1258     -1.012531     -1.012525     -1.012520     -1.012517  
1259     -1.036678     -1.036636     -1.036601     -1.036572  

[1260 rows x 333 columns]

In [8]:
test_list = ["Cardboard1", "Ceramic1", "Glass1", "Plastic1", "Rock1"]
e_test = e_data[(e_data["names"]=="Cardboard1" )|(e_data["names"]=="Ceramic1" )|(e_data["names"]=="Glass1") |(e_data["names"]=="Plastic1") |(e_data["names"]=="Rock1")].reset_index(drop=True)
e_test

names  Density  spectrum_0  spectrum_1  spectrum_2  spectrum_3  \
0    Cardboard1      0.7   -0.028709   -0.025573   -0.022161   -0.018525   
1    Cardboard1      0.7    0.005553    0.009694    0.013887    0.018083   
2    Cardboard1      0.7    0.038184    0.042790    0.047380    0.051909   
3    Cardboard1      0.7   -0.464907   -0.462942   -0.460760   -0.458399   
4    Cardboard1      0.7   -0.584556   -0.582479   -0.580313   -0.578093   
..          ...      ...         ...         ...         ...         ...   
445       Rock1      3.2   -0.009634   -0.009217   -0.008780   -0.008344   
446       Rock1      3.2   -0.016928   -0.016365   -0.015864   -0.015433   
447       Rock1      3.2   -0.998589   -0.999041   -0.999464   -0.999856   
448       Rock1      3.2   -1.014564   -1.015152   -1.015591   -1.015912   
449       Rock1      3.2   -1.000601   -1.000721   -1.000917   -1.001173   

     spectrum_4  spectrum_5  spectrum_6  spectrum_7  ...  spectrum_321  \
0     -0.014682   -0.010642   -0.006427   -0.002061  ...      0.599317   
1      0.022298    0.026552    0.030853    0.035206  ...      0.650668   
2      0.056409    0.060903    0.065401    0.069906  ...      0.700868   
3     -0.455878   -0.453210   -0.450416   -0.447522  ...     -0.028375   
4     -0.575820   -0.573494   -0.571121   -0.568704  ...     -0.206089   
..          ...         ...         ...         ...  ...           ...   
445   -0.007914   -0.007509   -0.007145   -0.006834  ...      0.176384   
446   -0.015058   -0.014742   -0.014487   -0.014291  ...      0.165443   
447   -1.000226   -1.000580   -1.000924   -1.001263  ...     -0.993987   
448   -1.016159   -1.016373   -1.016584   -1.016819  ...     -1.012611   
449   -1.001470   -1.001798   -1.002147   -1.002512  ...     -0.992938   

     spectrum_322  spectrum_323  spectrum_324  spectrum_325  spectrum_326  \
0        0.599639      0.599922      0.600171      0.600390      0.600583   
1        0.651063      0.651414      0.651725      0.652000      0.652243   
2        0.701222      0.701535      0.701811      0.702056      0.702271   
3       -0.027961     -0.027591     -0.027261     -0.026967     -0.026707   
4       -0.205748     -0.205446     -0.205178     -0.204942     -0.204734   
..            ...           ...           ...           ...           ...   
445      0.176582      0.176750      0.176892      0.177013      0.177115   
446      0.165632      0.165795      0.165935      0.166054      0.166157   
447     -0.993959     -0.993938     -0.993921     -0.993910     -0.993901   
448     -1.012574     -1.012541     -1.012513     -1.012488     -1.012466   
449     -0.992861     -0.992794     -0.992735     -0.992684     -0.992640   

     spectrum_327  spectrum_328  spectrum_329  spectrum_330  
0        0.600752      0.600899      0.601027      0.601132  
1        0.652458      0.652646      0.652808      0.652944  
2        0.702461      0.702627      0.702771      0.702891  
3       -0.026477     -0.026274     -0.026099     -0.025952  
4       -0.204551     -0.204390     -0.204252     -0.204137  
..            ...           ...           ...           ...  
445      0.177200      0.177272      0.177332      0.177380  
446      0.166245      0.166320      0.166384      0.166435  
447     -0.993896     -0.993893     -0.993891     -0.993891  
448     -1.012446     -1.012430     -1.012415     -1.012403  
449     -0.992602     -0.992569     -0.992542     -0.992519  

[450 rows x 333 columns]

In [9]:
e_train = e_data[(e_data["names"]!="Cardboard1")&(e_data["names"]!="Ceramic1" )&(e_data["names"]!="Glass1")&(e_data["names"]!="Plastic1") &(e_data["names"]!="Rock1")].reset_index(drop=True)
e_train

names  Density  spectrum_0  spectrum_1  spectrum_2  spectrum_3  \
0    Cardboard      0.7    0.058279    0.063007    0.067694    0.072298   
1    Cardboard      0.7    0.107668    0.112021    0.116560    0.121207   
2    Cardboard      0.7    0.091189    0.095456    0.099860    0.104353   
3    Cardboard      0.7    0.111236    0.114431    0.117930    0.121694   
4    Cardboard      0.7    0.048949    0.051882    0.055263    0.058999   
..         ...      ...         ...         ...         ...         ...   
805       Wood      0.8   -0.020559   -0.020252   -0.019827   -0.019304   
806       Wood      0.8   -0.141702   -0.141929   -0.141998   -0.141924   
807       Wood      0.8   -0.969075   -0.969072   -0.969058   -0.969057   
808       Wood      0.8   -1.010783   -1.010703   -1.010686   -1.010730   
809       Wood      0.8   -1.029769   -1.030050   -1.030271   -1.030452   

     spectrum_4  spectrum_5  spectrum_6  spectrum_7  ...  spectrum_321  \
0      0.076858    0.081422    0.086024    0.090695  ...      0.557489   
1      0.125941    0.130761    0.135658    0.140626  ...      0.610426   
2      0.108945    0.113654    0.118484    0.123433  ...      0.588477   
3      0.125711    0.129980    0.134483    0.139196  ...      0.611844   
4      0.063017    0.067271    0.071713    0.076300  ...      0.530075   
..          ...         ...         ...         ...  ...           ...   
805   -0.018699   -0.018044   -0.017370   -0.016704  ...      0.135658   
806   -0.141726   -0.141434   -0.141075   -0.140675  ...     -0.008360   
807   -0.969083   -0.969153   -0.969274   -0.969449  ...     -0.960065   
808   -1.010826   -1.010971   -1.011161   -1.011389  ...     -1.012643   
809   -1.030616   -1.030782   -1.030964   -1.031170  ...     -1.037113   

     spectrum_322  spectrum_323  spectrum_324  spectrum_325  spectrum_326  \
0        0.557749      0.557980      0.558187      0.558372      0.558535   
1        0.610694      0.610936      0.611154      0.611349      0.611523   
2        0.588641      0.588790      0.588924      0.589045      0.589153   
3        0.612121      0.612367      0.612586      0.612779      0.612950   
4        0.530425      0.530738      0.531018      0.531267      0.531489   
..            ...           ...           ...           ...           ...   
805      0.136021      0.136337      0.136612      0.136852      0.137061   
806     -0.008045     -0.007770     -0.007532     -0.007325     -0.007146   
807     -0.959989     -0.959924     -0.959869     -0.959823     -0.959784   
808     -1.012611     -1.012586     -1.012566     -1.012551     -1.012540   
809     -1.037013     -1.036925     -1.036849     -1.036784     -1.036727   

     spectrum_327  spectrum_328  spectrum_329  spectrum_330  
0        0.558680      0.558808      0.558920      0.559013  
1        0.611679      0.611817      0.611937      0.612038  
2        0.589249      0.589335      0.589409      0.589472  
3        0.613102      0.613235      0.613350      0.613446  
4        0.531685      0.531859      0.532009      0.532135  
..            ...           ...           ...           ...  
805      0.137242      0.137398      0.137532      0.137642  
806     -0.006990     -0.006856     -0.006743     -0.006649  
807     -0.959750     -0.959722     -0.959699     -0.959680  
808     -1.012531     -1.012525     -1.012520     -1.012517  
809     -1.036678     -1.036636     -1.036601     -1.036572  

[810 rows x 333 columns]

In [10]:
e_test_name = e_test["names"].to_numpy()
e_test = e_test.drop(columns = ["names"])
e_train = e_train.drop(columns = ["names"])

In [11]:
e_test

Density  spectrum_0  spectrum_1  spectrum_2  spectrum_3  spectrum_4  \
0        0.7   -0.028709   -0.025573   -0.022161   -0.018525   -0.014682   
1        0.7    0.005553    0.009694    0.013887    0.018083    0.022298   
2        0.7    0.038184    0.042790    0.047380    0.051909    0.056409   
3        0.7   -0.464907   -0.462942   -0.460760   -0.458399   -0.455878   
4        0.7   -0.584556   -0.582479   -0.580313   -0.578093   -0.575820   
..       ...         ...         ...         ...         ...         ...   
445      3.2   -0.009634   -0.009217   -0.008780   -0.008344   -0.007914   
446      3.2   -0.016928   -0.016365   -0.015864   -0.015433   -0.015058   
447      3.2   -0.998589   -0.999041   -0.999464   -0.999856   -1.000226   
448      3.2   -1.014564   -1.015152   -1.015591   -1.015912   -1.016159   
449      3.2   -1.000601   -1.000721   -1.000917   -1.001173   -1.001470   

     spectrum_5  spectrum_6  spectrum_7  spectrum_8  ...  spectrum_321  \
0     -0.010642   -0.006427   -0.002061    0.002423  ...      0.599317   
1      0.026552    0.030853    0.035206    0.039611  ...      0.650668   
2      0.060903    0.065401    0.069906    0.074422  ...      0.700868   
3     -0.453210   -0.450416   -0.447522   -0.444556  ...     -0.028375   
4     -0.573494   -0.571121   -0.568704   -0.566247  ...     -0.206089   
..          ...         ...         ...         ...  ...           ...   
445   -0.007509   -0.007145   -0.006834   -0.006579  ...      0.176384   
446   -0.014742   -0.014487   -0.014291   -0.014146  ...      0.165443   
447   -1.000580   -1.000924   -1.001263   -1.001600  ...     -0.993987   
448   -1.016373   -1.016584   -1.016819   -1.017094  ...     -1.012611   
449   -1.001798   -1.002147   -1.002512   -1.002889  ...     -0.992938   

     spectrum_322  spectrum_323  spectrum_324  spectrum_325  spectrum_326  \
0        0.599639      0.599922      0.600171      0.600390      0.600583   
1        0.651063      0.651414      0.651725      0.652000      0.652243   
2        0.701222      0.701535      0.701811      0.702056      0.702271   
3       -0.027961     -0.027591     -0.027261     -0.026967     -0.026707   
4       -0.205748     -0.205446     -0.205178     -0.204942     -0.204734   
..            ...           ...           ...           ...           ...   
445      0.176582      0.176750      0.176892      0.177013      0.177115   
446      0.165632      0.165795      0.165935      0.166054      0.166157   
447     -0.993959     -0.993938     -0.993921     -0.993910     -0.993901   
448     -1.012574     -1.012541     -1.012513     -1.012488     -1.012466   
449     -0.992861     -0.992794     -0.992735     -0.992684     -0.992640   

     spectrum_327  spectrum_328  spectrum_329  spectrum_330  
0        0.600752      0.600899      0.601027      0.601132  
1        0.652458      0.652646      0.652808      0.652944  
2        0.702461      0.702627      0.702771      0.702891  
3       -0.026477     -0.026274     -0.026099     -0.025952  
4       -0.204551     -0.204390     -0.204252     -0.204137  
..            ...           ...           ...           ...  
445      0.177200      0.177272      0.177332      0.177380  
446      0.166245      0.166320      0.166384      0.166435  
447     -0.993896     -0.993893     -0.993891     -0.993891  
448     -1.012446     -1.012430     -1.012415     -1.012403  
449     -0.992602     -0.992569     -0.992542     -0.992519  

[450 rows x 332 columns]

In [12]:
e_test_y = e_test["Density"]
e_test_x = e_test.drop(columns = ["Density"])

In [13]:
e_train_y = e_train["Density"].to_numpy()
e_train_x = e_train.drop(columns = ["Density"]).to_numpy()

In [14]:
e_train_y = np.reshape(e_train_y, (810, 1))

In [15]:
x, y = torch.from_numpy(e_train_x).float(), torch.from_numpy(e_train_y).float()

In [16]:
model = nn.Sequential(
    bnn.BayesLinear(prior_mu=0, prior_sigma=0.1, in_features=331, out_features=1024),
    nn.Sigmoid(),
    #nn.ReLU(),    

    bnn.BayesLinear(prior_mu=0, prior_sigma=0.1, in_features=1024, out_features=512),
    nn.Sigmoid(),    
    #nn.ReLU(),   
    
    bnn.BayesLinear(prior_mu=0, prior_sigma=0.1, in_features=512, out_features=256),
    nn.Sigmoid(),    
    #nn.ReLU(),   
    
    bnn.BayesLinear(prior_mu=0, prior_sigma=0.1, in_features=256, out_features=128),
    nn.Sigmoid(),    
    #nn.ReLU(),    
    
    
    bnn.BayesLinear(prior_mu=0, prior_sigma=0.1, in_features=128, out_features=64),
    nn.Sigmoid(),
    #nn.ReLU(),    
    
    
    bnn.BayesLinear(prior_mu=0, prior_sigma=0.1, in_features=64, out_features=32),
    nn.Sigmoid(),
    #nn.ReLU(),    


    bnn.BayesLinear(prior_mu=0, prior_sigma=0.1, in_features=32, out_features=9),
    nn.Sigmoid(),
    #nn.ReLU(),        
    
    
    bnn.BayesLinear(prior_mu=0, prior_sigma=0.1, in_features=9, out_features=1),
)

mse_loss = nn.MSELoss()
mae_loss = nn.L1Loss()
ce_loss = nn.CrossEntropyLoss()

kl_loss = bnn.BKLLoss(reduction='mean', last_layer_only=False)
optimizer = optim.Adam(model.parameters(), lr=0.001)

In [17]:
kl_weight = 0.01
#kl_weight = 1/len(x)

for step in range(150000):
    pre = model(x)
    mse = mse_loss(pre, y)
    kl = kl_loss(model)
    cost = mse + kl_weight*kl    
    optimizer.zero_grad()
    cost.backward()
    optimizer.step()
    print(str(step)+'- MSE : %2.6f, KL : %2.6f' % (mse.item(), kl.item()))
print('- MSE : %2.6f, KL : %2.6f' % (mse.item(), kl.item()))

0- MSE : 13.825629, KL : 0.032615
1- MSE : 12.598404, KL : 0.032654
2- MSE : 11.721119, KL : 0.032710
3- MSE : 12.073512, KL : 0.032774
4- MSE : 11.610566, KL : 0.032848
5- MSE : 10.940388, KL : 0.032921
6- MSE : 11.441033, KL : 0.032994
7- MSE : 11.474337, KL : 0.033069
8- MSE : 11.136048, KL : 0.033142
9- MSE : 14.570472, KL : 0.033215
10- MSE : 10.902247, KL : 0.033287
11- MSE : 12.132122, KL : 0.033357
12- MSE : 11.073717, KL : 0.033427
13- MSE : 12.624777, KL : 0.033495
14- MSE : 11.060628, KL : 0.033557
15- MSE : 11.762295, KL : 0.033618
16- MSE : 10.838450, KL : 0.033679
17- MSE : 10.903671, KL : 0.033739
18- MSE : 9.678731, KL : 0.033798
19- MSE : 10.736114, KL : 0.033855
20- MSE : 11.186031, KL : 0.033911
21- MSE : 10.443858, KL : 0.033965
22- MSE : 10.227810, KL : 0.034018
23- MSE : 9.796721, KL : 0.034068
24- MSE : 9.356706, KL : 0.034114
25- MSE : 12.347130, KL : 0.034159
26- MSE : 11.768606, KL : 0.034202
27- MSE : 10.838930, KL : 0.034245
28- MSE : 9.769854, KL : 0.034285

237- MSE : 6.083274, KL : 0.032665
238- MSE : 6.503534, KL : 0.032642
239- MSE : 6.232294, KL : 0.032620
240- MSE : 6.212547, KL : 0.032598
241- MSE : 6.526581, KL : 0.032576
242- MSE : 6.183912, KL : 0.032554
243- MSE : 6.635754, KL : 0.032532
244- MSE : 6.545656, KL : 0.032509
245- MSE : 6.232797, KL : 0.032487
246- MSE : 6.701356, KL : 0.032465
247- MSE : 6.234866, KL : 0.032442
248- MSE : 5.942887, KL : 0.032420
249- MSE : 6.425943, KL : 0.032397
250- MSE : 6.525707, KL : 0.032375
251- MSE : 6.653761, KL : 0.032352
252- MSE : 6.620386, KL : 0.032329
253- MSE : 6.069558, KL : 0.032306
254- MSE : 6.465854, KL : 0.032284
255- MSE : 5.950643, KL : 0.032261
256- MSE : 6.419836, KL : 0.032239
257- MSE : 6.680836, KL : 0.032216
258- MSE : 6.287226, KL : 0.032193
259- MSE : 5.941369, KL : 0.032171
260- MSE : 6.328794, KL : 0.032148
261- MSE : 5.975063, KL : 0.032126
262- MSE : 5.913636, KL : 0.032103
263- MSE : 6.137981, KL : 0.032080
264- MSE : 6.905575, KL : 0.032057
265- MSE : 6.018858,

472- MSE : 5.678012, KL : 0.027068
473- MSE : 5.688230, KL : 0.027044
474- MSE : 5.904481, KL : 0.027020
475- MSE : 5.664526, KL : 0.026996
476- MSE : 5.846344, KL : 0.026972
477- MSE : 5.669926, KL : 0.026948
478- MSE : 5.757979, KL : 0.026925
479- MSE : 5.746562, KL : 0.026901
480- MSE : 5.664000, KL : 0.026877
481- MSE : 6.010071, KL : 0.026853
482- MSE : 5.921449, KL : 0.026829
483- MSE : 5.721168, KL : 0.026806
484- MSE : 5.695031, KL : 0.026782
485- MSE : 5.683509, KL : 0.026759
486- MSE : 5.666556, KL : 0.026735
487- MSE : 5.694108, KL : 0.026712
488- MSE : 5.699302, KL : 0.026688
489- MSE : 5.761595, KL : 0.026665
490- MSE : 5.684228, KL : 0.026641
491- MSE : 5.666409, KL : 0.026617
492- MSE : 5.678127, KL : 0.026594
493- MSE : 5.664002, KL : 0.026570
494- MSE : 5.746627, KL : 0.026546
495- MSE : 5.670844, KL : 0.026523
496- MSE : 5.679674, KL : 0.026499
497- MSE : 5.808926, KL : 0.026475
498- MSE : 5.663962, KL : 0.026452
499- MSE : 5.694759, KL : 0.026428
500- MSE : 5.668389,

708- MSE : 5.677714, KL : 0.021857
709- MSE : 5.668101, KL : 0.021838
710- MSE : 5.664154, KL : 0.021819
711- MSE : 5.686158, KL : 0.021799
712- MSE : 5.667500, KL : 0.021780
713- MSE : 5.664090, KL : 0.021761
714- MSE : 5.745413, KL : 0.021741
715- MSE : 5.801333, KL : 0.021722
716- MSE : 5.692944, KL : 0.021703
717- MSE : 6.081563, KL : 0.021684
718- MSE : 5.674777, KL : 0.021664
719- MSE : 5.679199, KL : 0.021645
720- MSE : 5.665962, KL : 0.021625
721- MSE : 5.664428, KL : 0.021605
722- MSE : 5.699677, KL : 0.021586
723- MSE : 5.665769, KL : 0.021566
724- MSE : 5.702876, KL : 0.021547
725- MSE : 5.667933, KL : 0.021527
726- MSE : 5.699767, KL : 0.021508
727- MSE : 5.819282, KL : 0.021489
728- MSE : 5.709218, KL : 0.021469
729- MSE : 5.673088, KL : 0.021450
730- MSE : 5.694868, KL : 0.021430
731- MSE : 5.699107, KL : 0.021411
732- MSE : 5.692257, KL : 0.021392
733- MSE : 5.730800, KL : 0.021373
734- MSE : 5.708832, KL : 0.021353
735- MSE : 5.680740, KL : 0.021334
736- MSE : 5.727374,

948- MSE : 5.693823, KL : 0.017824
949- MSE : 5.674338, KL : 0.017810
950- MSE : 5.790126, KL : 0.017796
951- MSE : 5.666345, KL : 0.017782
952- MSE : 5.689225, KL : 0.017768
953- MSE : 5.669267, KL : 0.017754
954- MSE : 5.704443, KL : 0.017740
955- MSE : 5.667691, KL : 0.017727
956- MSE : 5.664433, KL : 0.017713
957- MSE : 5.664122, KL : 0.017699
958- MSE : 5.747280, KL : 0.017685
959- MSE : 5.759325, KL : 0.017671
960- MSE : 5.664805, KL : 0.017657
961- MSE : 5.685088, KL : 0.017643
962- MSE : 5.853429, KL : 0.017630
963- MSE : 5.664233, KL : 0.017616
964- MSE : 5.672119, KL : 0.017602
965- MSE : 5.748870, KL : 0.017589
966- MSE : 5.688648, KL : 0.017575
967- MSE : 5.785964, KL : 0.017562
968- MSE : 5.687809, KL : 0.017549
969- MSE : 5.665107, KL : 0.017535
970- MSE : 5.796749, KL : 0.017521
971- MSE : 5.693316, KL : 0.017508
972- MSE : 5.704701, KL : 0.017495
973- MSE : 5.694265, KL : 0.017481
974- MSE : 5.832002, KL : 0.017468
975- MSE : 5.670739, KL : 0.017455
976- MSE : 5.738569,

...

149050- MSE : 0.002596, KL : 1.618026
149051- MSE : 0.063928, KL : 1.618018
149052- MSE : 0.012160, KL : 1.618026
149053- MSE : 0.019037, KL : 1.618036
149054- MSE : 0.002281, KL : 1.618047
149055- MSE : 0.101498, KL : 1.618057
149056- MSE : 0.000550, KL : 1.618068
149057- MSE : 0.000399, KL : 1.618076
149058- MSE : 0.064631, KL : 1.618081
149059- MSE : 0.004595, KL : 1.618073
149060- MSE : 0.037057, KL : 1.618063
149061- MSE : 0.000353, KL : 1.618047
149062- MSE : 0.000394, KL : 1.618032
149063- MSE : 0.006209, KL : 1.618014
149064- MSE : 0.001891, KL : 1.617994
149065- MSE : 0.006477, KL : 1.617974
149066- MSE : 0.017106, KL : 1.617950
149067- MSE : 0.042219, KL : 1.617929
149068- MSE : 0.056081, KL : 1.617919
149069- MSE : 0.018554, KL : 1.617904
149070- MSE : 0.002493, KL : 1.617885
149071- MSE : 0.119361, KL : 1.617867
149072- MSE : 0.075506, KL : 1.617834
149073- MSE : 0.060059, KL : 1.617798
149074- MSE : 0.000480, KL : 1.617753
149075- MSE : 0.013451, KL : 1.617711
149076- MSE 

149270- MSE : 0.001825, KL : 1.616922
149271- MSE : 0.001677, KL : 1.616939
149272- MSE : 0.004060, KL : 1.616952
149273- MSE : 0.002160, KL : 1.616960
149274- MSE : 0.008413, KL : 1.616962
149275- MSE : 0.004071, KL : 1.616964
149276- MSE : 0.016712, KL : 1.616963
149277- MSE : 0.002583, KL : 1.616962
149278- MSE : 0.001071, KL : 1.616957
149279- MSE : 0.010887, KL : 1.616950
149280- MSE : 0.000481, KL : 1.616940
149281- MSE : 0.009098, KL : 1.616928
149282- MSE : 0.008866, KL : 1.616911
149283- MSE : 0.000511, KL : 1.616894
149284- MSE : 0.022160, KL : 1.616875
149285- MSE : 0.001293, KL : 1.616847
149286- MSE : 0.047124, KL : 1.616819
149287- MSE : 0.001454, KL : 1.616786
149288- MSE : 0.000390, KL : 1.616754
149289- MSE : 0.005036, KL : 1.616722
149290- MSE : 0.020387, KL : 1.616690
149291- MSE : 0.038092, KL : 1.616664
149292- MSE : 0.198804, KL : 1.616644
149293- MSE : 0.045821, KL : 1.616627
149294- MSE : 0.000447, KL : 1.616614
149295- MSE : 0.043462, KL : 1.616601
149296- MSE 

149488- MSE : 0.088709, KL : 1.613005
149489- MSE : 0.000781, KL : 1.613017
149490- MSE : 0.005344, KL : 1.613029
149491- MSE : 0.005520, KL : 1.613039
149492- MSE : 0.000442, KL : 1.613047
149493- MSE : 0.000623, KL : 1.613054
149494- MSE : 0.034489, KL : 1.613058
149495- MSE : 0.009778, KL : 1.613057
149496- MSE : 0.000550, KL : 1.613078
149497- MSE : 0.002723, KL : 1.613097
149498- MSE : 0.000345, KL : 1.613113
149499- MSE : 0.000910, KL : 1.613127
149500- MSE : 0.000981, KL : 1.613137
149501- MSE : 0.002917, KL : 1.613144
149502- MSE : 0.000656, KL : 1.613149
149503- MSE : 0.028730, KL : 1.613150
149504- MSE : 0.001892, KL : 1.613152
149505- MSE : 0.008624, KL : 1.613152
149506- MSE : 0.000655, KL : 1.613147
149507- MSE : 0.033074, KL : 1.613141
149508- MSE : 0.015489, KL : 1.613134
149509- MSE : 0.214047, KL : 1.613127
149510- MSE : 0.000674, KL : 1.613125
149511- MSE : 0.044401, KL : 1.613122
149512- MSE : 0.009082, KL : 1.613117
149513- MSE : 0.087540, KL : 1.613107
149514- MSE 

149706- MSE : 0.000234, KL : 1.612250
149707- MSE : 0.021196, KL : 1.612236
149708- MSE : 0.157960, KL : 1.612223
149709- MSE : 0.205002, KL : 1.612214
149710- MSE : 0.076684, KL : 1.612205
149711- MSE : 0.001952, KL : 1.612187
149712- MSE : 0.119388, KL : 1.612173
149713- MSE : 0.030261, KL : 1.612166
149714- MSE : 0.000333, KL : 1.612165
149715- MSE : 0.276506, KL : 1.612167
149716- MSE : 0.000570, KL : 1.612163
149717- MSE : 0.000383, KL : 1.612162
149718- MSE : 0.001651, KL : 1.612161
149719- MSE : 0.058168, KL : 1.612162
149720- MSE : 0.014448, KL : 1.612171
149721- MSE : 0.005934, KL : 1.612182
149722- MSE : 0.002548, KL : 1.612194
149723- MSE : 0.014233, KL : 1.612206
149724- MSE : 0.004115, KL : 1.612218
149725- MSE : 0.054504, KL : 1.612230
149726- MSE : 0.090252, KL : 1.612243
149727- MSE : 0.006801, KL : 1.612259
149728- MSE : 0.001650, KL : 1.612272
149729- MSE : 0.077406, KL : 1.612283
149730- MSE : 0.025995, KL : 1.612291
149731- MSE : 0.021740, KL : 1.612296
149732- MSE 

149926- MSE : 0.005492, KL : 1.615675
149927- MSE : 0.018414, KL : 1.615712
149928- MSE : 0.011412, KL : 1.615747
149929- MSE : 0.043102, KL : 1.615779
149930- MSE : 0.052288, KL : 1.615819
149931- MSE : 0.103403, KL : 1.615862
149932- MSE : 0.022318, KL : 1.615908
149933- MSE : 0.044632, KL : 1.615951
149934- MSE : 0.003513, KL : 1.615993
149935- MSE : 0.014866, KL : 1.616031
149936- MSE : 0.041806, KL : 1.616068
149937- MSE : 0.009587, KL : 1.616095
149938- MSE : 0.084819, KL : 1.616120
149939- MSE : 0.033578, KL : 1.616135
149940- MSE : 0.034717, KL : 1.616149
149941- MSE : 0.030742, KL : 1.616156
149942- MSE : 0.010632, KL : 1.616158
149943- MSE : 0.001913, KL : 1.616160
149944- MSE : 0.123149, KL : 1.616162
149945- MSE : 0.134860, KL : 1.616169
149946- MSE : 0.031738, KL : 1.616176
149947- MSE : 0.001508, KL : 1.616177
149948- MSE : 0.004978, KL : 1.616177
149949- MSE : 0.000996, KL : 1.616176
149950- MSE : 0.002389, KL : 1.616174
149951- MSE : 0.014580, KL : 1.616170
149952- MSE 

In [18]:
x_test, y_test = torch.from_numpy(e_test_x.to_numpy()).float(), torch.from_numpy(e_test_y.to_numpy()).float()

In [19]:
pred_tt = model(x_test)
for i in range(len(y_test)):
    print(e_test_name[i], f"Predicted: {round(float(pred_tt[i]), 1)} - Actual: {round(float(y_test[i]), 1)}")

Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7


In [20]:
torch.save(model, 'bbn_density.pth')
bnn = torch.load('bbn_density.pth')

In [21]:
pred_tt = bnn(x_test)
for i in range(len(y_test)):
    print(e_test_name[i], f"Predicted: {round(float(pred_tt[i]), 1)} - Actual: {round(float(y_test[i]), 1)}")

Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
Cardboard1 Predicted: 0.7 - Actual: 0.7
